In [25]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import geopandas
from branca.colormap import linear
import branca.colormap as cmp
import folium
from shapely.ops import nearest_points
from shapely.geometry import *


In [44]:
neighbour_df = geopandas.read_file('../input/dubai-neighborhoods/dubai.geojson')
stations_df = geopandas.read_file('../input/dubai-neighborhoods/dubai_metro_stations.geojson')
venues_df = pd.read_csv('../input/dubai-neighborhoods/dubai_venues.csv')

In [45]:
venues_df = geopandas.GeoDataFrame(venues_df, 
            geometry = geopandas.points_from_xy(venues_df['Venue Longitude'], venues_df['Venue Latitude']), 
            crs="EPSG:4326")
venues_df                        

COMM_NUM      CNAME_E  Sector  Community Latitude  Community Longitude  \
0          111  AL CORNICHE       1           25.277837            55.302557   
1          111  AL CORNICHE       1           25.277837            55.302557   
2          111  AL CORNICHE       1           25.277837            55.302557   
3          111  AL CORNICHE       1           25.277837            55.302557   
4          111  AL CORNICHE       1           25.277837            55.302557   
...        ...          ...     ...                 ...                  ...   
2950       981     MUGATRAH       9           24.797001            55.213668   
2951       981     MUGATRAH       9           24.797001            55.213668   
2952       981     MUGATRAH       9           24.797001            55.213668   
2953       981     MUGATRAH       9           24.797001            55.213668   
2954       981     MUGATRAH       9           24.797001            55.213668   

                      Venue Id                              Venue  \
0     4ccafdcaaa25a35d0e100b0f                           Miyako 京   
1     4d76451348b7f04dabadf2f5                          Al Dawaar   
2     4c0190f4b58376b05062443c                        The Kitchen   
3     4df4e8d9aeb7170aa2f5e7c5                       Club Olympus   
4     4bb0bf0ef964a52055593ce3  Hyatt Regency Dubai (حياة ريجنسي)   
...                        ...                                ...   
2950  5065a73be4b07b978819581a                  Bab Al Shams Pool   
2951  4ccd9137ba0a548148154459                   Le Dune Pizzeria   
2952  4c0a3b83a1b32d7f93f098f0                         Satori Spa   
2953  4c9e14fa54c8a1cd73d2894b                             Masala   
2954  4cfa10f9c51fa1cdd58dde2b                    Al Qudra Racing   

      Venue Latitude  Venue Longitude       Venue Category  ...  \
0          25.278925        55.304343  Japanese Restaurant  ...   
1          25.279111        55.304414           Restaurant  ...   
2          25.279047        55.304267           Restaurant  ...   
3          25.278362        55.304438                  Gym  ...   
4          25.279240        55.304364                Hotel  ...   
...              ...              ...                  ...  ...   
2950       24.816112        55.229698           Hotel Pool  ...   
2951       24.816438        55.229525                Diner  ...   
2952       24.816145        55.230104                 Pool  ...   
2953       24.815922        55.230647    Indian Restaurant  ...   
2954       24.818367        55.246473                 Farm  ...   

      Stats UsersCount  Stats CheckinsCount  Rating  Rating Color  \
0                  213                  406     8.7        73CF42   
1                  533                  651     8.5        73CF42   
2                  242                  437     8.3        73CF42   
3                  167                  749     8.2        73CF42   
4                 4498                 8660     8.1        73CF42   
...                ...                  ...     ...           ...   
2950               173                  236     NaN           NaN   
2951                78                   83     NaN           NaN   
2952                64                   69     NaN           NaN   
2953               135                  145     NaN           NaN   
2954                67                   85     NaN           NaN   

     Rating Signals                                                Url  \
0              42.0  http://dubai.regency.hyatt.com/en/hotel/dining...   
1              72.0  http://dubai.regency.hyatt.com/en/hotel/dining...   
2              26.0  http://dubai.regency.hyatt.com/en/hotel/dining...   
3              18.0  http://dubai.regency.hyatt.com/en/hotel/dining...   
4             366.0                     http://dubai.regency.hyatt.com   
...             ...                                                ...   
2950            NaN                                             

In [4]:
#setup map
dubai_geo = r'../input/dubai-neighborhoods/dubai.geojson'
dubai_lat = 25.05
dubai_long = 55.11
map1 = folium.Map([dubai_lat, dubai_long], tiles='CartoDB positron', zoom_start=10.5)


fg_stations = folium.FeatureGroup(name='Metro Stations', overlay=True, control=True, show=True ).add_to(map1)
fg_venues = folium.FeatureGroup(name='Venues', overlay=True, control=True, show=True ).add_to(map1)

for index, row in stations_df.iterrows():
    popup_text = '{}, {}'.format(row['STATION_NAME'], row['COMMUNITY_NAME'])
    popup_text = folium.Popup(popup_text, parse_html=True)    
    folium.CircleMarker(location=(row['LAT_STATION'],
                                  row['LON_STATION']),   
                        radius=2,
                        color='#ff0000',
                        popup=popup_text,
                        parse_html=False,
                        fill=False).add_to(fg_stations)
    
for index, row in venues_df.iterrows():
    popup_text = '{}, {}'.format(row['Venue'], row['CNAME_E'])
    popup_text = folium.Popup(popup_text, parse_html=True)    
    folium.CircleMarker(location=(row['Venue Latitude'],
                                  row['Venue Longitude']),  
                        radius=2,
                        color='#0000ff',
                        popup=popup_text,
                        parse_html=False,
                        fill=False).add_to(fg_venues)

folium.LayerControl().add_to(map1)
map1.save('MetroMap.html')
#IFrame(src='./MetroMap.html', width=900, height=500)
map1

In [46]:
def calculate_nearest(row, destination, val, col="geometry"):
    # 1 - create unary union    
    dest_unary = destination['geometry'].unary_union
    # 2 - find closest point
    nearest_geom = nearest_points(row[col], dest_unary)
    # 3 - Find the corresponding geom
    match_geom = destination.loc[destination.geometry 
                == nearest_geom[1]]
    # 4 - get the corresponding value
    match_value = match_geom[val].to_numpy()[0]
    return match_value

In [47]:
# Get the nearest geometry
venues_df["nearest_geometry"] = venues_df.apply(calculate_nearest, destination=stations_df, val="geometry", axis=1)
# Get the nearest metro station name
venues_df["nearest_station"] = venues_df.apply(calculate_nearest, destination=stations_df, val="STATION_NAME", axis=1)

In [51]:
venues_df.to_csv('./venues_station.csv')  

# Visualise the nearest stations

In [28]:
# Create LineString Geometry
venues_df['line'] = venues_df.apply(lambda row: LineString([row['geometry'], row['nearest_geometry']]), axis=1)
# Create Line Geodataframe
line_df = venues_df[["Venue", "nearest_station", "line"]].set_geometry('line')
# Set the Coordinate reference
line_df.crs = "epsg:4326"

In [40]:
map2 = folium.Map([dubai_lat, dubai_long],zoom_start = 12,  tiles="CartoDb dark_matter")

locs_stations = zip(stations_df.LON_STATION, stations_df.LAT_STATION)
locs_points = zip(venues_df['Venue Longitude'], venues_df['Venue Latitude'])

for location in locs_stations:
    folium.CircleMarker(location=location, 
              color="red",  radius=4).add_to(map2)
    
for location in locs_points:
    folium.CircleMarker(location=location, 
              color="white", radius=2).add_to(map2)
    
folium.GeoJson(line_df).add_to(map2)

map2.save("line_map2.html")
map2